In [1]:
# Allow multiple displays per cell
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [2]:
%load_ext dotenv

In [3]:
import os

In [4]:
!pwd
!ls -l ./

/datadrive01/prj/AzureChestXRayNoAML/code
total 560
-rwxrwxrwx 1 loginvm001 loginvm001 265591 May 24 05:52 00_create_docker_image.html
-rwxrwxrwx 1 loginvm001 loginvm001  21678 May 24 05:52 00_create_docker_image.ipynb
drwxrwxrwx 4 loginvm001 loginvm001   4096 May 24 05:27 01_DataPrep
drwxrwxrwx 3 loginvm001 loginvm001   4096 May 24 05:36 02_Model
drwxrwxrwx 2 loginvm001 loginvm001   4096 May 20 05:08 docker_history
-rwxrwxrwx 1 loginvm001 loginvm001 256265 Jan 24 17:52 edit_python_files.html
-rwxrwxrwx 1 loginvm001 loginvm001   6868 May 24 00:56 edit_python_files.ipynb
drwxrwxrwx 3 loginvm001 loginvm001   4096 May 24 00:56 src


In [5]:
%%writefile .env
# This cell is tagged `parameters`
# Please modify the values below as you see fit

# Your docker login and image repository name
docker_login = 'georgedockeraccount'
image_tag = "/chestxray-no-aml-gpu-root-account"
image_version = '1.0.3'

Overwriting .env


In [6]:
%dotenv
os.getenv('image_version')
dockerfile_name = 'dockerfile'+ '_' + os.getenv('image_version')

'1.0.3'

In [7]:
%%writefile ./../docker/$dockerfile_name

FROM nvidia/cuda:9.0-cudnn7-devel
#FROM nvidia/cuda:9.0-cudnn7-devel-ubuntu16.04

MAINTAINER George Iordanescu <ghiordan@microsoft.com>
#based on https://github.com/keras-team/keras/blob/master/docker/Dockerfile

# Install system packages
RUN apt-get update && apt-get install -y --no-install-recommends \
      apt-utils \
      bzip2 \
      g++ \
      git \
      graphviz \
      libgl1-mesa-glx \
      libhdf5-dev \
      openmpi-bin \
      wget \
      ssh \
      rsync && \
    rm -rf /var/lib/apt/lists/*

# Install conda
ENV CONDA_DIR /opt/conda
ENV PATH $CONDA_DIR/bin:$PATH

RUN wget --quiet --no-check-certificate https://repo.continuum.io/miniconda/Miniconda3-4.2.12-Linux-x86_64.sh && \
    echo "c59b3dd3cad550ac7596e0d599b91e75d88826db132e4146030ef471bb434e9a *Miniconda3-4.2.12-Linux-x86_64.sh" | sha256sum -c - && \
    /bin/bash /Miniconda3-4.2.12-Linux-x86_64.sh -f -b -p $CONDA_DIR && \
    rm Miniconda3-4.2.12-Linux-x86_64.sh && \
    echo export PATH=$CONDA_DIR/bin:'$PATH' > /etc/profile.d/conda.sh 
        
#https://docs.microsoft.com/en-us/azure/storage/common/storage-use-azcopy-linux
# https://docs.microsoft.com/en-us/azure/storage/common/storage-use-azcopy-linux#download-and-install-azcopy
# https://www.microsoft.com/net/download/linux-package-manager/ubuntu16-04/runtime-2.1.2
RUN wget -q https://packages.microsoft.com/config/ubuntu/16.04/packages-microsoft-prod.deb && \
    dpkg -i packages-microsoft-prod.deb && \ 
    apt-get install  -y --no-install-recommends apt-transport-https && \
    apt-get update && \
    apt-get install  -y --no-install-recommends aspnetcore-runtime-2.1  && \
    mkdir /tmp/azcopy && \
    wget -O /tmp/azcopy/azcopy.tar.gz https://aka.ms/downloadazcopyprlinux &&  \
    tar -xf /tmp/azcopy/azcopy.tar.gz -C /tmp/azcopy &&  \
    /tmp/azcopy/install.sh && \
    rm -rf /tmp/azcopy

# Install Python packages and keras
# ENV NB_USER keras
# ENV NB_UID 1000

# RUN useradd -m -s /bin/bash -N -u $NB_UID $NB_USER && \
#     chown $NB_USER $CONDA_DIR -R && \
#     mkdir -p /src && \
#     chown $NB_USER /src

# USER $NB_USER
RUN mkdir -p /sr

ARG python_version=3.6

# TF 1.13:cuda 10.0, cudnn 7 
RUN conda install -y python=${python_version} && \
    pip install --upgrade pip && \
    pip install \
      sklearn_pandas \
      scikit-image \
      tensorflow-gpu==1.12.2 \
      tensorflow-tensorboard \
      matplotlib \
      numpy && \
    conda install \
      bcolz \
      h5py \
      matplotlib \
      mkl \
      nose \
      notebook=5.6.0 \
      opencv \
      Pillow \
      pandas \
      pydot \
      pygpu \
      pyyaml \
      requests \
      scikit-learn \
      six \
      tqdm \
      pytorch torchvision cudatoolkit=9.0 -c pytorch && \
    conda install -c conda-forge imageio && \
    git clone git://github.com/keras-team/keras.git /src && pip install -e /src[tests] && \
    pip install git+git://github.com/keras-team/keras.git && \
    pip install git+https://github.com/aleju/imgaug && \
    pip install git+https://www.github.com/keras-team/keras-contrib.git && \
    conda clean -yt     

#ADD theanorc /home/keras/.theanorc

ENV PYTHONPATH='/src/:$PYTHONPATH'

WORKDIR /src

EXPOSE 8888

# CMD jupyter notebook --port=8888 --ip=0.0.0.0


Overwriting ./../docker/dockerfile_1.0.3


In [8]:
%dotenv
docker_image_name = os.getenv('docker_login') + os.getenv('image_tag') + ':' + os.getenv('image_version')
docker_file_location = os.path.join(*(['.', '..','docker', dockerfile_name]))
working_path = '.'

docker_image_name
docker_file_location

'georgedockeraccount/chestxray-no-aml-gpu-root-account:1.0.3'

'./../docker/dockerfile_1.0.3'

In [9]:
!mkdir -p ./docker_history
!cp $docker_file_location ./docker_history/

In [10]:
!echo docker build -t $docker_image_name -f $docker_file_location $working_path
!docker build -t $docker_image_name -f $docker_file_location $working_path

docker build -t georgedockeraccount/chestxray-no-aml-gpu-root-account:1.0.3 -f ./../docker/dockerfile_1.0.3 .
Sending build context to Docker daemon  5.078MB
Step 1/13 : FROM nvidia/cuda:9.0-cudnn7-devel
 ---> 9852e0e6efd1
Step 2/13 : MAINTAINER George Iordanescu <ghiordan@microsoft.com>
 ---> Using cache
 ---> adf79349315c
Step 3/13 : RUN apt-get update && apt-get install -y --no-install-recommends       apt-utils       bzip2       g++       git       graphviz       libgl1-mesa-glx       libhdf5-dev       openmpi-bin       wget       ssh       rsync &&     rm -rf /var/lib/apt/lists/*
 ---> Using cache
 ---> c162a8788c58
Step 4/13 : ENV CONDA_DIR /opt/conda
 ---> Using cache
 ---> 88ef3fabde23
Step 5/13 : ENV PATH $CONDA_DIR/bin:$PATH
 ---> Using cache
 ---> fb903159cd3f
Step 6/13 : RUN wget --quiet --no-check-certificate https://repo.continuum.io/miniconda/Miniconda3-4.2.12-Linux-x86_64.sh &&     echo "c59b3dd3cad550ac7596e0d599b91e75d88826db132e4146030ef471bb434e9a *Miniconda3-4.2.12

  Stored in directory: /root/.cache/pip/wheels/de/63/64/3699be2a9d0ccdb37c7f16329acf3863fd76eda58c39c737af
  Stored in directory: /root/.cache/pip/wheels/5c/2e/7e/a1d4d4fcebe6c381f378ce7743a3ced3699feb89bcfbdadadd
  Stored in directory: /root/.cache/pip/wheels/7c/06/54/bc84598ba1daf8f970247f550b175aaaee85f68b4b0c5ab2c6
  Stored in directory: /root/.cache/pip/wheels/ee/98/38/46cbcc5a93cfea5492d19c38562691ddb23b940176c14f7b48


  Stored in directory: /root/.cache/pip/wheels/50/ae/f9/d2b189788efcf61d1ee0e36045476735c838898eef1cad6e29
Successfully built networkx gast termcolor absl-py html5lib
Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda:

The following NEW packages will be INSTALLED:

    attrs:             19.1.0-py36_1                               
    backcall:          0.1.0-py36_0                                
    bcolz:             1.2.1-py36h04863e7_0                        
    blas:              1.0-mkl                                     
    bleach:            3.1.0-py36_0                                
    blosc:             1.16.3-hd408876_0                           
    bokeh:             1.1.0-py36_0                                
    bzip2:             1.0.6-h14c3975_5                            
    cairo:             1.14.12-h8948797_3                          
    chardet:           3.0.4-py36_1      

jasper-2.0.14- 100% |###############################| Time: 0:00:00  65.66 MB/s
libedit-3.1-he 100% |###############################| Time: 0:00:00  66.52 MB/s
libpng-1.6.37- 100% |###############################| Time: 0:00:00  66.04 MB/s
libxml2-2.9.9- 100% |###############################| Time: 0:00:00  64.58 MB/s
pandoc-2.2.3.2 100% |###############################| Time: 0:00:00  64.63 MB/s
readline-7.0-h 100% |###############################| Time: 0:00:00  65.56 MB/s
tk-8.6.8-hbc83 100% |###############################| Time: 0:00:00  51.36 MB/s
zeromq-4.3.1-h 100% |###############################| Time: 0:00:00  61.29 MB/s
zstd-1.3.7-h0b 100% |###############################| Time: 0:00:00  66.91 MB/ss
blosc-1.16.3-h 100% |###############################| Time: 0:00:00  54.48 MB/s
dbus-1.13.6-h7 100% |###############################| Time: 0:00:00  65.16 MB/s
freetype-2.9.1 100% |###############################| Time: 0:00:00  72.99 MB/s
gstreamer-1.14 100% |##################

bcolz-1.2.1-py 100% |###############################| Time: 0:00:00  67.31 MB/s
Solving environment: ...working... done

## Package Plan ##

  environment location: /opt/conda

  added / updated specs:
    - imageio


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2019.3.9   |       hecc5488_0         146 KB  conda-forge
    certifi-2019.3.9           |           py36_0         149 KB  conda-forge
    conda-4.6.14               |           py36_0         2.1 MB  conda-forge
    cryptography-2.6.1         |   py36h72c5cf5_0         606 KB  conda-forge
    imageio-2.5.0              |           py36_0         3.4 MB  conda-forge
    libedit-3.1.20170329       |    hf8c457e_1001         172 KB  conda-forge
    ncurses-6.1                |    hf484d3e_1002         1.3 MB  conda-forge
    openssl-1.1.1b             |       h14c3975_1         4.0 MB  conda-forge
    python-3.6

  Stored in directory: /root/.cache/pip/wheels/68/34/52/2a6e08e030cef8b3671898f34cecb12750cc4b96ebfe66fe67
  Stored in directory: /root/.cache/pip/wheels/e4/9e/28/59d0a23800e49808f17920c5922252c661966ca4a36db5ee38
Successfully built pytest-pep8 pytest-cache
  Running setup.py develop for Keras
  Cloning git://github.com/keras-team/keras.git to /tmp/pip-req-build-ea7ke66w
  Running command git clone -q git://github.com/keras-team/keras.git /tmp/pip-req-build-ea7ke66w
  Stored in directory: /tmp/pip-ephem-wheel-cache-_wvmi62c/wheels/e6/02/ad/5e8e1a5824af71082e2260fe7e2eaa1b745c34706e6ff0a14b
Successfully built Keras
  Cloning https://github.com/aleju/imgaug to /tmp/pip-req-build-ztclfmsx
  Running command git clone -q https://github.com/aleju/imgaug /tmp/pip-req-build-ztclfmsx
  Stored in directory: /tmp/pip-ephem-wheel-cache-fe7t18d4/wheels/9c/f6/aa/41dcf2f29cc1de1da4ad840ef5393514bead64ac9e644260ff
Successfully built imgaug
  Cloning https://www.github.com/keras-team/keras-contrib.git 

scipy-1.2.1-py36h7c811a0_0.tar.bz2          17.7 MB
opencv-3.4.2-py36h6fd60c2_1.tar.bz2           11 KB
kiwisolver-1.1.0-py36he6710b0_0.tar.bz2       90 KB
click-7.0-py36_0.tar.bz2                     118 KB
tqdm-4.31.1-py36_1.tar.bz2                    69 KB
prometheus_client-0.6.0-py36_0.tar.bz2        70 KB
pcre-8.43-he6710b0_0.tar.bz2                 260 KB
qt-5.9.7-h5867ecd_1.tar.bz2                 85.9 MB
pip-9.0.1-py36_1.tar.bz2                     1.7 MB
glib-2.56.2-hd408876_0.tar.bz2               5.0 MB
attrs-19.1.0-py36_1.tar.bz2                   56 KB
pyrsistent-0.14.11-py36h7b6447c_0.tar.bz2      90 KB
prompt_toolkit-2.0.9-py36_0.tar.bz2          493 KB
parso-0.4.0-py_0.tar.bz2                      66 KB
msgpack-python-0.6.1-py36hfd86e86_1.tar.bz2      92 KB
chardet-3.0.4-py36_1.tar.bz2                 189 KB
python-3.6.2-0.tar.bz2                      16.5 MB
decorator-4.4.0-py36_1.tar.bz2                18 KB
testpath-0.4.2-py36_0.tar.bz2                 91 KB
six-1.10

Removing intermediate container 295033aa45cd
 ---> 009e39f616d4
Step 11/13 : ENV PYTHONPATH='/src/:$PYTHONPATH'
 ---> Running in 99f205530f9f
Removing intermediate container 99f205530f9f
 ---> e61f93c3b1a1
Step 12/13 : WORKDIR /src
 ---> Running in 5298423dddad
Removing intermediate container 5298423dddad
 ---> 229abd1400a8
Step 13/13 : EXPOSE 8888
 ---> Running in c2489f923ce7
Removing intermediate container c2489f923ce7
 ---> 0cc273c2775f
Successfully built 0cc273c2775f
Successfully tagged georgedockeraccount/chestxray-no-aml-gpu-root-account:1.0.3


In [11]:
!docker push $docker_image_name

The push refers to repository [docker.io/georgedockeraccount/chestxray-no-aml-gpu-root-account]

1ff92445: Preparing 
9b876185: Preparing 
455e02b2: Preparing 
54cf6c0c: Preparing 
16fdc3cb: Preparing 
d89c03b2: Preparing 
6c26f9e7: Preparing 
fe741405: Preparing 
a476f8a1: Preparing 
0a19db94: Preparing 
e996c345: Preparing 
c11b1a82: Preparing 
aa7554e3: Preparing 
57aea3bf: Preparing 


ff92445: Pushing  1.779GB/5.816GB5APushing    414MB/5.816GBPushing  1.346GB/5.816GBPushing  1.399GB/5.816GB

ff92445: Pushing  3.625GB/5.816GBPushing  1.868GB/5.816GBPushing  3.517GB/5.816GB

ff92445: Pushing  5.501GB/5.816GBPushing  3.956GB/5.816GBPushing  4.625GB/5.816GB

ff92445: Pushed   5.903GB/5.816GB1.0.3: digest: sha256:753d973f2e50791db04042312f03b206ff0659f398b6bee117c9637efadbf4ab size: 3474


In [12]:
!echo nvidia-docker run -i -t --rm --name azurechestxray_container -p 10003:8888 -v '$(pwd)':/local_dir:rw $docker_image_name /bin/bash -c '"/opt/conda/bin/jupyter notebook --notebook-dir=/local_dir --ip=0.0.0.0 --port=8888 --no-browser --allow-root"'

nvidia-docker run -i -t --rm --name azurechestxray_container -p 10003:8888 -v $(pwd):/local_dir:rw georgedockeraccount/chestxray-no-aml-gpu-root-account:1.0.3 /bin/bash -c "/opt/conda/bin/jupyter notebook --notebook-dir=/local_dir --ip=0.0.0.0 --port=8888 --no-browser --allow-root"


In [13]:
!jupyter nbconvert --to html 00_create_docker_image.ipynb

[NbConvertApp] Converting notebook 00_create_docker_image.ipynb to html
[NbConvertApp] Writing 335280 bytes to 00_create_docker_image.html
